<h1>Table of Contents<span class="tocSkip"></span></h1>
<div class="toc"><ul class="toc-item"><li><ul class="toc-item"><li><ul class="toc-item"><li><span><a href="#imports" data-toc-modified-id="imports-0.0.1"><span class="toc-item-num">0.0.1&nbsp;&nbsp;</span>imports</a></span></li><li><span><a href="#methods" data-toc-modified-id="methods-0.0.2"><span class="toc-item-num">0.0.2&nbsp;&nbsp;</span>methods</a></span></li></ul></li></ul></li><li><span><a href="#Planning" data-toc-modified-id="Planning-1"><span class="toc-item-num">1&nbsp;&nbsp;</span>Planning</a></span></li><li><span><a href="#Scrape-candidate-IDs" data-toc-modified-id="Scrape-candidate-IDs-2"><span class="toc-item-num">2&nbsp;&nbsp;</span>Scrape candidate IDs</a></span><ul class="toc-item"><li><span><a href="#Gather-IDs-from-page" data-toc-modified-id="Gather-IDs-from-page-2.1"><span class="toc-item-num">2.1&nbsp;&nbsp;</span>Gather IDs from page</a></span><ul class="toc-item"><li><ul class="toc-item"><li><span><a href="#they-updated-their-site,-so-no-more-pagification--:-)" data-toc-modified-id="they-updated-their-site,-so-no-more-pagification--:-)-2.1.0.1"><span class="toc-item-num">2.1.0.1&nbsp;&nbsp;</span>they updated their site, so no more pagification  : )</a></span></li><li><span><a href="#ID-scrape-complete,-save-objects" data-toc-modified-id="ID-scrape-complete,-save-objects-2.1.0.2"><span class="toc-item-num">2.1.0.2&nbsp;&nbsp;</span>ID scrape complete, save objects</a></span></li></ul></li></ul></li></ul></li><li><span><a href="#make-api-calls" data-toc-modified-id="make-api-calls-3"><span class="toc-item-num">3&nbsp;&nbsp;</span>make api calls</a></span><ul class="toc-item"><li><span><a href="#4-piece-API-call-methods" data-toc-modified-id="4-piece-API-call-methods-3.1"><span class="toc-item-num">3.1&nbsp;&nbsp;</span>4-piece API call methods</a></span></li><li><span><a href="#Cleaner-stack-structure-method" data-toc-modified-id="Cleaner-stack-structure-method-3.2"><span class="toc-item-num">3.2&nbsp;&nbsp;</span>Cleaner stack-structure method</a></span><ul class="toc-item"><li><span><a href="#working-checkpoint:" data-toc-modified-id="working-checkpoint:-3.2.1"><span class="toc-item-num">3.2.1&nbsp;&nbsp;</span>working checkpoint:</a></span></li></ul></li></ul></li><li><span><a href="#Parse-XML-into-nested-list-of-nested-dictionaries" data-toc-modified-id="Parse-XML-into-nested-list-of-nested-dictionaries-4"><span class="toc-item-num">4&nbsp;&nbsp;</span>Parse XML into nested list of nested dictionaries</a></span></li><li><span><a href="#data-ready-for-graphing" data-toc-modified-id="data-ready-for-graphing-5"><span class="toc-item-num">5&nbsp;&nbsp;</span>data ready for graphing</a></span></li></ul></div>

### imports

In [1]:
import pandas as pd
import selenium
import random
import time
import os
import io
import json 
import pickle
import requests
import xmltodict
import pprint
import json
import config


import xml.etree.ElementTree as ET
from io import StringIO
from random import randint
from selenium import webdriver 
from selenium.webdriver.common.by import By 
from selenium.webdriver.support.ui import WebDriverWait 
from selenium.webdriver.support.ui import Select
from selenium.webdriver.support import expected_conditions as EC 
from selenium.common.exceptions import TimeoutException

we'll be <s>scraping</s> requesting data from opensecrets.org (Center for Responsive Politics). specifically we're looking at each congressmember's campaign donations received from lobbying groups, organized by industry.

- data taken from Center for Responsive Politics @ opensecrets.org

### methods

In [2]:
def short_wait():
    time.sleep(random.randint(5,10))

# hardcoding note: have to path to driver to launch selenium
def launch_driver(): # i should figure out a way to dynamically code the path so it launches on anyone's machine
    driver = webdriver.Chrome(executable_path='/Users/mark/Documents/flatiron/projects/congress_bribes/graphing_congressional_lobbying/graphing_congress_lobbying_industries/chromedriver', options=option)
    return driver # wouldn't that require keeping chromedriver executable in the project folder?


def get_properties(element):
    return driver.execute_script('var items = {}; for (index = 0; index < arguments[0].attributes.length; ++index) { items[arguments[0].attributes[index].name] = arguments[0].attributes[index].value }; return items;', element)
# outputs the properties of passed element (if locatable on driver page)
# ||||||||||| obtaining data

def extract_links_from_page(): # extracts URLs for each member's page from list_of_members page
    odds = driver.find_elements_by_class_name('odd')
    evens = driver.find_elements_by_class_name('even')
    rows = odds + evens
    current_page_urls = []
    for row in rows: # extract link to congressmember's page
        a = row.find_element_by_tag_name('a')
        current_page_urls.append(a.get_attribute('href'))
    return current_page_urls # returns a list of URLS

def go_next_page():
    driver.find_element_by_id('DataTables_Table_0_next').click()
    
def update_url(url): # saves a couple of clicks per member, which is good. websites get angry if you click a lot
    tar = 'https://www.opensecrets.org/members-of-congress/industries?cid=N00007360&cycle=2020&recs=0&type=C'
    return tar[:59]+url[-13:]+tar[72:] # put unique member_id into updated url

def get_all_links():
    urls = []
    for i in range(11): # there's 11 pages. could code this better to a while, check for Next page = True
        page_urls = extract_links_from_page()
        urls += page_urls
        print(f'|||||scraped page {i+1}')
        print(f'# urls: {len(urls)}')
        short_wait()
        go_next_page()
        short_wait()
    print(f'storing {len(urls)} URLs in list')
    clean_urls = []
    for url in urls:
        clean_urls.append(update_url(url))
    return clean_urls

def get_member_ids(urls): # returns list of strings
    ids = []
    for url in urls:
        ids.append(url[63:72])
    return ids
        

def download_csv(): # downloads the relevant .csv to your default Downloads folder
    print('waiting 3-5 to load') # you'll have 535 new .csvs
    time.sleep(random.randint(3,5))
    holder = driver.find_element_by_class_name('table-title')
    holder.find_element_by_tag_name('a').click() # clicks download csv button
    
def extract_bribery_records(urls): # pass it your cleaned URL list
    print('|||beginning bribery extraction|||')
    for c, url in enumerate(urls): # loops through all 535 members, downloads
        print('waiting 4-7 before visiting...') # waiting is time consuming
        time.sleep(random.randint(4,7)) # but so is being IP banned from your target site
        driver.get(url)
        download_csv()
        print(f'downloaded {c} member\'s bribes')

        # API method
def get_responses(urls):
    responses = []
    for c, url in enumerate(urls):
        mem_id = url[63:72] # slice the candidate's unique ID from the links we gather earlier
        print(mem_id)
        req = 'https://www.opensecrets.org/api/?method=candIndustry&cid=N00007360&cycle=2018&apikey='+key
        new = req[:57]+mem_id+req[66:73]+'2020'+req[77:] # splice into requests URL
        r = requests.get(new)
        time.sleep(random.randint(1,2))
        if r.status_code!=200:
            print('___---___---___ Bad Request')
        responses.append(r)
        print(f'{c} requests made')
    print('|||done requesting|||')
    return responses
        
# ||||||||||| cleaning data
def read_all_csvs(path): # reads all csvs in working directory to list of dataframes
    dfs = []
    c=0 # this method.... i'm not using this anymore
    c+=1 # filename slicing, add name to each dataframe
    df = pd.read_csv(file) # file is the filename string
    df['name'] = file[15:file.index('N0')-1].replace(' ','_')
    dfs.append(df)
    print(f'read {c} dataframes. returning list...')
    return dfs
            
def pickle_obj(obj, filename): # designed with list of strings in mind, but i guess it works for other stuff? cool
    urls = open(filename,"w+")
    with open(filename, 'wb') as f:
        pickle.dump(obj, f)
def unpickle_obj(filename):
    with open(filename, 'rb') as f:
        return pickle.load(f)
    
    
# |||||||||||||||||||||||||||||||||||| API XML cleaning

def write_resps_to_xml(resps): # pass the list of responses
    for c,resp in enumerate(resps):
        name = resp.text[1:4] + str(c) + '.xml' # arbitrary filename, xml extension
        with open(name, 'wb') as f: # we can extract the member's name from the XML later
            f.write(resp.content) # save the file to working directory
            print(f'wrote {c} resps to directory')
#         time.sleep(1)
            
def read_xmls_to_dict(): # reads all .XMLs in working directory
    members = {} # returns dictionary with nested member-dictionaries (holdin)
    directory = os.path.join("c:\\",path)
    for root,dirs,files in os.walk(directory):
        for file in files: # initially i despaired at the lack of JSON in the API's responses
            if file.endswith(".xml"): # but ElementTree is super helpful here
                mem_dict = {}
                tree = ET.parse(file)
                root = tree.getroot()
                mem_dict['name'] = root[0].attrib['cand_name'] # set identifier
                mem_dict['party'] = mem_dict['name'][-2]
                for industries_tag in root: # there's only 1
                    for indu in industries_tag: # however many different industries donated to this candidate
                        in_dict = {}
                        in_dict['code'] = indu.attrib['industry_code']
                        in_dict['name'] = indu.attrib['industry_name']
                        in_dict['indiv'] = indu.attrib['indivs']
                        in_dict['PAC'] = indu.attrib['pacs']
                        in_dict['total'] = indu.attrib['total']
                        mem_dict[in_dict['name']] = in_dict # nest industry into member
                members[mem_dict['name']] = mem_dict # nest member into holder dict
    if len(members)==535: print('we\'re good')
    return members 
    
    

# Planning

- for each member of congress, get:
    - name, party, list of industries
    - for each industry, get:
        - name, dollars donated, financial breakdown
        
we'll be using data from the Center for Responsive Politics (opensecrets.org).
- scrape IDs from webpage
- use IDs in api calls
- parse XML responses to list of nested dictionaries
- save list for graphing in next step

# Scrape candidate IDs
- their API has a getLegislators method
    - but that only returns the current congress's IDs
    - if we want past data, we can *gently* scrape IDs from the site and substitute the proper year in the call URL

In [3]:
pwd

'/Users/mark/Documents/flatiron/projects/congress_bribes/graphing_congressional_lobbying/graphing_congress_lobbying_industries'

In [4]:
# variables for driver launch
base_url = 'https://www.opensecrets.org/members-of-congress/members-list?cong_no=116&cycle=2020&sort=N'
option = webdriver.ChromeOptions() # you'll need the proper chrome drivers for Selenium
option.add_argument(' — incognito', )
# substitute your proper working directory
path = '/Users/mark/Documents/flatiron/projects/congress_bribes/graphing_congressional_lobbying/graphing_congress_lobbying_industries/'

In [5]:
# help(option.add_argument)

In [128]:
driver = launch_driver()

In [53]:
key = config.api_key
# you'll need to register on opensecrets.org to get an API key

## Gather IDs from page
#### they updated their site, so no more pagification  : )

In [129]:
driver.get("https://www.opensecrets.org/members-of-congress/members-list?cong_no=116&cycle=2018&sort=N")


In [136]:
def get_ids(): # returns list of lists of strings
    out = [ [], [] ] # [ [house], [senate] ]
    c=0 # error counter
    table = driver.find_element_by_class_name('Congress.l-primary') # all links on one page, no need for pagification
    blocks = table.find_elements_by_tag_name('p') # 26, one for each letter
    for block in blocks: # block structure: alternating <a>, <i> tags at same depth
        members_names = block.find_elements_by_tag_name('a')
        members_details = block.find_elements_by_tag_name('i')
        for name, details in zip(members_names, members_details):
            url = name.get_attribute('href')
            mem_id = url[-9:] # slice the unique ID out of the link
            tagline = details.text
            if 'District' in tagline: # house
                out[0].append(mem_id)
            elif 'Senate' in tagline: # senate
                out[1].append(mem_id)
            else:
                print('|||| At Large congressmember ||||')
                print(tagline) #
                c+=1
                out[0].append(mem_id)
    if c>0: print(f'{c} errors') # looks like the errors are with Guam, Puerto Rico
    return out # territories, etc. that's okay. I'll... just put them in House, why not.

In [137]:
id_list = get_ids() # i don't think lobbyists target territories, but good to include for completion

|||| At Large congressmember ||||
Guam Democrat, At Large
|||| At Large congressmember ||||
Puerto Rico Third Party, At Large
|||| At Large congressmember ||||
Virgin Islands Democrat, At Large
|||| At Large congressmember ||||
American Samoa Republican, At Large
4 errors


In [138]:
print(len(id_list[0]), len(id_list[1])) # 535 + 4 at large, works out great

439 100


In [139]:
print(type(id_list), len(id_list), len(id_list[0]), len(id_list[1]), '\n', id_list[0][0])
# looking good

<class 'list'> 2 439 100 
 N00036633


In [10]:
filen = 'all_congress_ids'

In [141]:
pickle_obj(id_list, filen) # saved to working directory

#### ID scrape complete, save objects

In [11]:
t = unpickle_obj(filen)
id_list = t

In [71]:
# check for duplicates
all_ids = id_list[0]+id_list[1]
print(len(all_ids))
c = 0
for a in all_ids:
    for b in all_ids:
        if a == b: c+=1
print(c) # no duplicates in ID list

539
539


# make api calls

In [8]:
key = config.api_key
# the API has a 200-per-period limit on the candIndustry method we're using
# so until they get back to me, i'll use a piecemeal split-method approach to finish it in 3 periods

## 4-piece API call methods
- the 'one for everything' method i tried was messy and gave me duplicates, so let's do this cleanly

In [6]:
apk = config.api_key
def make_industry_request(cand_id):
    ''' Argument: candidate id string
        Returns: request
    ''' 
    rst = "https://www.opensecrets.org/api/?method=candIndustry&cid="+cand_id+"&cycle=2018&apikey="+apk
    resp = requests.get(rst) # make the request
    if 'call limit' in resp.text:
        print('call limit reached! breaking to fix')
        return 'call limit reached' # to break in main method
    return resp
                
    
def get_first_200(responses, id_list, apk):
    print('first 200 of house')
    ids = id_list[0][:200] # designate first 200 of house
    for c, cand_id in enumerate(ids):
        resp = make_industry_request(cand_id)
        responses[0].append(resp)
        print(f'{c} / 200')
    print(len(responses[0]))
    return responses

def get_next_200(responses, id_list, apk):
    print('next 200 of house')
    ids = id_list[0][200:400] # designate next 200 of house
    for c, cand_id in enumerate(ids):
        resp = make_industry_request(cand_id)
        responses[0].append(resp)
        print(f'{c} / 200')
    print(len(responses[0]))
    return responses

def get_35_house(responses, id_list, apk):
    print('remaining 35 of house')
    ids = id_list[0][400:] # designate next 35 of house
    for c, cand_id in enumerate(ids):
        resp = make_industry_request(cand_id)
        responses[0].append(resp)
        print(f'{c} / {len(ids)}')
    print(len(responses[0]))
    return responses

def get_all_senate(responses, id_list, apk):
    print('all 105 of senate')
    ids = id_list[1] # designate senate
    for c, cand_id in enumerate(ids):
        resp = make_industry_request(cand_id)
        responses[1].append(resp)
        print(f'{c} / {len(ids)}')
    print(len(responses[1]))
    return responses
# precise but verbose

In [7]:
a = [1,2,3]
while a:
    print(a.pop(0))
    

1
2
3


## Cleaner stack-structure method
runs much better than the original

In [8]:
def call_api(id_list, resps, processed_ids):
    ''' Arguments:
            list of unique member IDs, list of responses, list of IDs called so far
        Returns:
            id_list (200 fewer), resps (200 more), processed_ids (200 more)
    '''
    print(f'House: {len(resps[0])}  Senate: {len(resps[1])}')
    c = 0 # daily call limit
    while id_list[0]:
        cid = id_list[0].pop(0) # take the first House id
        response = make_industry_request(cid) # call API
        if response == 'call limit reached':
            return 'call limit error, breaking'
        resps[0].append(response)
        processed_ids[0].append(cid)
        print(f'{c+1} / 200')
        c+=1
        if c >= 200: break
    if c < 200: # handles the transition on 3rd run (getting 35 House and 100 Senate)
        while id_list[1]:
            cid = id_list[1].pop(0)
            response = make_industry_request(cid)
            if response == 'call limit reached':
                return 'call limit error, breaking'
            resps[1].append(response)
            processed_ids[1].append(cid)
            print(f'{c+1} / 200')
            c+=1
            if c >= 200: break
    print(f'current calls: {c}   House: {len(resps[0])}  Senate: {len(resps[1])}')
    return id_list, resps, processed_ids # keep track of these 3 as we go

In [12]:
len(id_list[0])

439

In [13]:
resps = [[],[]] # id_list is the updated len=539
processed_ids = [[],[]] # redo these in the correct format

In [14]:
# about 3 seconds per request
# much more server-friendly than scraping
id_list, resps, processed_ids = call_api(id_list, resps, processed_ids)

House: 0  Senate: 0
1 / 200
2 / 200
3 / 200
4 / 200
5 / 200
6 / 200
7 / 200
8 / 200
9 / 200
10 / 200
11 / 200
12 / 200
13 / 200
14 / 200
15 / 200
16 / 200
17 / 200
18 / 200
19 / 200
20 / 200
21 / 200
22 / 200
23 / 200
24 / 200
25 / 200
26 / 200
27 / 200
28 / 200
29 / 200
30 / 200
31 / 200
32 / 200
33 / 200
34 / 200
35 / 200
36 / 200
37 / 200
38 / 200
39 / 200
40 / 200
41 / 200
42 / 200
43 / 200
44 / 200
45 / 200
46 / 200
47 / 200
48 / 200
49 / 200
50 / 200
51 / 200
52 / 200
53 / 200
54 / 200
55 / 200
56 / 200
57 / 200
58 / 200
59 / 200
60 / 200
61 / 200
62 / 200
63 / 200
64 / 200
65 / 200
66 / 200
67 / 200
68 / 200
69 / 200
70 / 200
71 / 200
72 / 200
73 / 200
74 / 200
75 / 200
76 / 200
77 / 200
78 / 200
79 / 200
80 / 200
81 / 200
82 / 200
83 / 200
84 / 200
85 / 200
86 / 200
87 / 200
88 / 200
89 / 200
90 / 200
91 / 200
92 / 200
93 / 200
94 / 200
95 / 200
96 / 200
97 / 200
98 / 200
99 / 200
100 / 200
101 / 200
102 / 200
103 / 200
104 / 200
105 / 200
106 / 200
107 / 200
108 / 200
109 / 20

In [17]:
pickle_obj(id_list, 'id_list')
pickle_obj(resps, 'resps')
pickle_obj(processed_ids, 'processed_ids')

In [18]:
len(resps[0])

200

In [19]:
print(len(id_list[0]),len(resps[0]),len(processed_ids[0]))

239 200 200


In [20]:
# 2nd run
id_list, resps, processed_ids = call_api(id_list, resps, processed_ids)

House: 200  Senate: 0
1 / 200
2 / 200
3 / 200
4 / 200
5 / 200
6 / 200
7 / 200
8 / 200
9 / 200
10 / 200
11 / 200
12 / 200
13 / 200
14 / 200
15 / 200
16 / 200
17 / 200
18 / 200
19 / 200
20 / 200
21 / 200
22 / 200
23 / 200
24 / 200
25 / 200
26 / 200
27 / 200
28 / 200
29 / 200
30 / 200
31 / 200
32 / 200
33 / 200
34 / 200
35 / 200
36 / 200
37 / 200
38 / 200
39 / 200
40 / 200
41 / 200
42 / 200
43 / 200
44 / 200
45 / 200
46 / 200
47 / 200
48 / 200
49 / 200
50 / 200
51 / 200
52 / 200
53 / 200
54 / 200
55 / 200
56 / 200
57 / 200
58 / 200
59 / 200
60 / 200
61 / 200
62 / 200
63 / 200
64 / 200
65 / 200
66 / 200
67 / 200
68 / 200
69 / 200
70 / 200
71 / 200
72 / 200
73 / 200
74 / 200
75 / 200
76 / 200
77 / 200
78 / 200
79 / 200
80 / 200
81 / 200
82 / 200
83 / 200
84 / 200
85 / 200
86 / 200
87 / 200
88 / 200
89 / 200
90 / 200
91 / 200
92 / 200
93 / 200
94 / 200
95 / 200
96 / 200
97 / 200
98 / 200
99 / 200
100 / 200
101 / 200
102 / 200
103 / 200
104 / 200
105 / 200
106 / 200
107 / 200
108 / 200
109 / 

In [21]:
print(len(id_list[0]),len(resps[0]),len(processed_ids[0]))

39 400 400


In [22]:
#2nd save
pickle_obj(id_list, 'id_list')
pickle_obj(resps, 'resps')
pickle_obj(processed_ids, 'processed_ids')

In [23]:
print(len(id_list[0]),len(resps[0]),len(processed_ids[0]))

39 400 400


In [24]:
# 3rd run
id_list, resps, processed_ids = call_api(id_list, resps, processed_ids)

House: 400  Senate: 0
1 / 200
2 / 200
3 / 200
4 / 200
5 / 200
6 / 200
7 / 200
8 / 200
9 / 200
10 / 200
11 / 200
12 / 200
13 / 200
14 / 200
15 / 200
16 / 200
17 / 200
18 / 200
19 / 200
20 / 200
21 / 200
22 / 200
23 / 200
24 / 200
25 / 200
26 / 200
27 / 200
28 / 200
29 / 200
30 / 200
31 / 200
32 / 200
33 / 200
34 / 200
35 / 200
36 / 200
37 / 200
38 / 200
39 / 200
40 / 200
41 / 200
42 / 200
43 / 200
44 / 200
45 / 200
46 / 200
47 / 200
48 / 200
49 / 200
50 / 200
51 / 200
52 / 200
53 / 200
54 / 200
55 / 200
56 / 200
57 / 200
58 / 200
59 / 200
60 / 200
61 / 200
62 / 200
63 / 200
64 / 200
65 / 200
66 / 200
67 / 200
68 / 200
69 / 200
70 / 200
71 / 200
72 / 200
73 / 200
74 / 200
75 / 200
76 / 200
77 / 200
78 / 200
79 / 200
80 / 200
81 / 200
82 / 200
83 / 200
84 / 200
85 / 200
86 / 200
87 / 200
88 / 200
89 / 200
90 / 200
91 / 200
92 / 200
93 / 200
94 / 200
95 / 200
96 / 200
97 / 200
98 / 200
99 / 200
100 / 200
101 / 200
102 / 200
103 / 200
104 / 200
105 / 200
106 / 200
107 / 200
108 / 200
109 / 

In [25]:
print(len(id_list[0]),len(resps[0]),len(processed_ids[0]))

0 439 439


In [26]:
# 3rd save
pickle_obj(id_list, 'id_list')
pickle_obj(resps, 'resps')
pickle_obj(processed_ids, 'processed_ids')

### working checkpoint:
- new stack method is doing good, but while testing it i used 4/200 of today's calls
    - it didn't break on a None like i wanted it to
    - so we've got len(200), but 4 Nones. these mis-called IDs should be found at the end of processed_ids
            - pop four nones from resps[0]
            - pop four relevant ids from processed_ into a holder list
            - make api calls with those 4

In [108]:
pickle_obj(id_list, 'id_list_new')
pickle_obj(resps, 'resps_new')
pickle_obj(processed_ids, 'processed_ids_new')

In [1]:
# len(id_list[0])

In [8]:
# a case:switch method. kinda.
def populate_responses(resps, id_list, apk): # resps should be empty. [ [], [] ] structure
    if len(resps[0]) < 198: 
        resps = get_first_200(resps, id_list, apk)
    elif len(resps[0]) >= 198 and len(resps[0]) < 398:
        resps = get_next_200(resps, id_list, apk)
    elif len(resps[0]) >= 398 and len(resps[0]) < 439:
        resps = get_35_house(resps, id_list, apk)
    elif len(resps[1]) < 105:
        print('populating senate')
        resps = get_all_senate(resps, id_list, apk)
    print(f'house: {len(resps[0])} / 435   senate: {len(resps[1])} / 105')
    return resps # we'll have to run this 3 over 3 periods

In [9]:
# resps = [[],[]]

In [ ]:
# i think i could have cleaned this process up by handling them in a stack structure
# pass id_list, resps, processed_id_list (all same format of list)
# for 200: take id_list[0], make call, put in resps, pop() to processed_.
# when no more in id_list[0], move to [1].
# yeah, that would have been cleaner, more resistant to mismatch-breakdowns with if >=

# i did exactly this, works great. i love stacks

In [16]:
# 1
print(f"start 1: {len(resps[0])}, {len(resps[1])}")
resps = populate_responses(resps, id_list, apk)
print(f"end: {len(resps[0])}, {len(resps[1])}")

start 1: 199, 0
next 200 of house
0 / 200
1 / 200
2 / 200
3 / 200
4 / 200
5 / 200
6 / 200
7 / 200
8 / 200
9 / 200
10 / 200
11 / 200
12 / 200
13 / 200
14 / 200
15 / 200
16 / 200
17 / 200
18 / 200
19 / 200
20 / 200
21 / 200
22 / 200
23 / 200
24 / 200
25 / 200
26 / 200
27 / 200
28 / 200
29 / 200
30 / 200
31 / 200
32 / 200
33 / 200
34 / 200
35 / 200
36 / 200
37 / 200
38 / 200
39 / 200
40 / 200
41 / 200
42 / 200
43 / 200
44 / 200
45 / 200
46 / 200
47 / 200
48 / 200
49 / 200
50 / 200
51 / 200
52 / 200
53 / 200
54 / 200
55 / 200
56 / 200
57 / 200
58 / 200
59 / 200
60 / 200
61 / 200
62 / 200
63 / 200
64 / 200
65 / 200
66 / 200
67 / 200
68 / 200
69 / 200
70 / 200
71 / 200
72 / 200
73 / 200
74 / 200
75 / 200
76 / 200
77 / 200
78 / 200
79 / 200
80 / 200
81 / 200
82 / 200
83 / 200
84 / 200
85 / 200
86 / 200
87 / 200
88 / 200
89 / 200
90 / 200
91 / 200
92 / 200
93 / 200
94 / 200
95 / 200
96 / 200
97 / 200
98 / 200
99 / 200
100 / 200
101 / 200
102 / 200
103 / 200
104 / 200
105 / 200
106 / 200
107 / 

In [17]:
pickle_obj(resps, '400_so_far')

In [8]:
resps = unpickle_obj('400_so_far')

In [9]:
resps[0]

[{'name': 'Ralph Abraham (R)',
  'party': 'R',
  'id': 'N00036633',
  'Health Professionals': {'code': 'H01',
   'name': 'Health Professionals',
   'indiv': '32400',
   'pac': '55500',
   'total': '87900'},
  'Crop Production & Basic Processing': {'code': 'A01',
   'name': 'Crop Production & Basic Processing',
   'indiv': '30100',
   'pac': '52250',
   'total': '82350'},
  'Agricultural Services/Products': {'code': 'A07',
   'name': 'Agricultural Services/Products',
   'indiv': '750',
   'pac': '37500',
   'total': '38250'},
  'General Contractors': {'code': 'C01',
   'name': 'General Contractors',
   'indiv': '29100',
   'pac': '4500',
   'total': '33600'},
  'Air Transport': {'code': 'M01',
   'name': 'Air Transport',
   'indiv': '0',
   'pac': '30500',
   'total': '30500'},
  'Leadership PACs': {'code': 'Q03',
   'name': 'Leadership PACs',
   'indiv': '0',
   'pac': '29750',
   'total': '29750'},
  'Defense Aerospace': {'code': 'D01',
   'name': 'Defense Aerospace',
   'indiv': '0',

In [11]:
p = []
for res in resps[0]:
    p.append(type(res))
print(len(set(p)), set(p))

3 {<class 'NoneType'>, <class 'requests.models.Response'>, <class 'dict'>}


In [10]:
len(resps[0])

NameError: name 'resps' is not defined

In [12]:
resps = unpickle_obj('first_200')

In [13]:
# 2
print(f"start 2: {len(resps[0])}, {len(resps[1])}")
resps = populate_responses(resps, id_list, apk)
print(f"end: {len(resps[0])}, {len(resps[1])}")

start 2: 198, 0
first 200 of house
0 / 200


KeyboardInterrupt: 

In [55]:
len(resps[0])

430

In [11]:
resps = unpickle_obj('next_400')

In [12]:
len(resps[0])

397

In [14]:
type(resps[0][-1])

dict

In [17]:
resps[0]

[{'name': 'Ralph Abraham (R)',
  'party': 'R',
  'id': 'N00036633',
  'Health Professionals': {'code': 'H01',
   'name': 'Health Professionals',
   'indiv': '32400',
   'pac': '55500',
   'total': '87900'},
  'Crop Production & Basic Processing': {'code': 'A01',
   'name': 'Crop Production & Basic Processing',
   'indiv': '30100',
   'pac': '52250',
   'total': '82350'},
  'Agricultural Services/Products': {'code': 'A07',
   'name': 'Agricultural Services/Products',
   'indiv': '750',
   'pac': '37500',
   'total': '38250'},
  'General Contractors': {'code': 'C01',
   'name': 'General Contractors',
   'indiv': '29100',
   'pac': '4500',
   'total': '33600'},
  'Air Transport': {'code': 'M01',
   'name': 'Air Transport',
   'indiv': '0',
   'pac': '30500',
   'total': '30500'},
  'Leadership PACs': {'code': 'Q03',
   'name': 'Leadership PACs',
   'indiv': '0',
   'pac': '29750',
   'total': '29750'},
  'Defense Aerospace': {'code': 'D01',
   'name': 'Defense Aerospace',
   'indiv': '0',

In [19]:
resps = unpickle_obj('400_so_far')

In [23]:
resps[-1]

[]

In [20]:
p = []
for r in resps[0]:
    p.append(type(r))
print(len(set(p)), set(p))

3 {<class 'NoneType'>, <class 'requests.models.Response'>, <class 'dict'>}


In [27]:
len(resps[0])

399

In [33]:
resps[0][198:] # from index 198 onwards, so 199 from the first day. t

[<Response [200]>,
 <Response [200]>,
 <Response [200]>,
 <Response [200]>,
 <Response [200]>,
 <Response [200]>,
 <Response [200]>,
 <Response [200]>,
 <Response [200]>,
 <Response [200]>,
 <Response [200]>,
 <Response [200]>,
 <Response [200]>,
 <Response [200]>,
 <Response [200]>,
 <Response [200]>,
 <Response [200]>,
 <Response [200]>,
 <Response [200]>,
 <Response [200]>,
 <Response [200]>,
 <Response [200]>,
 <Response [200]>,
 <Response [200]>,
 <Response [200]>,
 <Response [200]>,
 <Response [200]>,
 <Response [200]>,
 <Response [200]>,
 <Response [200]>,
 <Response [200]>,
 <Response [200]>,
 <Response [200]>,
 <Response [200]>,
 <Response [200]>,
 <Response [200]>,
 <Response [200]>,
 <Response [200]>,
 <Response [200]>,
 <Response [200]>,
 <Response [200]>,
 <Response [200]>,
 <Response [200]>,
 <Response [200]>,
 <Response [200]>,
 <Response [200]>,
 <Response [200]>,
 <Response [200]>,
 <Response [200]>,
 <Response [200]>,
 <Response [200]>,
 <Response [200]>,
 <Response [

In [37]:
import copy

In [38]:
unf = copy.deepcopy(resps[0][198:])

In [ ]:
for r in resps

In [83]:
unfmems[0]

AttributeError: 'list' object has no attribute 'keys'

In [24]:
resps[0].append({'placeholder':'yes'}) # get the length to 400
resps[0].append({'placeholder':'yes'}) # so the populate() doesn't think it's still on day 2
resps[0].append({'placeholder':'yes'})
len(resps[0])

400

In [25]:
# 3
print(f"start 3: {len(resps[0])}, {len(resps[1])}")
resps = populate_responses(resps, id_list, apk)
print(f"end: {len(resps[0])}, {len(resps[1])}")
pickle_obj(resps, 'complete_430')
pickle_obj(resps, 'full_data_430')

start 3: 400, 0
remaining 35 of house
0 / 30
1 / 30
2 / 30
3 / 30
4 / 30
5 / 30
6 / 30
7 / 30
8 / 30
9 / 30
10 / 30
11 / 30
12 / 30
13 / 30
14 / 30
15 / 30
16 / 30
17 / 30
18 / 30
19 / 30
20 / 30
21 / 30
22 / 30
23 / 30
24 / 30
25 / 30
26 / 30
27 / 30
28 / 30
29 / 30
430
house: 430 / 435   senate: 0 / 105
end: 430, 0


In [30]:
# 4
print(f"start 3: {len(resps[0])}, {len(resps[1])}")
resps = populate_responses(resps, id_list, apk)
print(f"end: {len(resps[0])}, {len(resps[1])}")
pickle_obj(resps, 'complete_430')
pickle_obj(resps, 'full_data_430')

start 3: 432, 0
populating senate
all 105 of senate
0 / 105
1 / 105
2 / 105
3 / 105
4 / 105
5 / 105
6 / 105
7 / 105
8 / 105
9 / 105
10 / 105
11 / 105
12 / 105
13 / 105
14 / 105
15 / 105
16 / 105
17 / 105
18 / 105
19 / 105
20 / 105
21 / 105
22 / 105
23 / 105
24 / 105
25 / 105
26 / 105
27 / 105
28 / 105
29 / 105
30 / 105
31 / 105
32 / 105
33 / 105
34 / 105
35 / 105
36 / 105
37 / 105
38 / 105
39 / 105
40 / 105
41 / 105
42 / 105
43 / 105
44 / 105
45 / 105
46 / 105
47 / 105
48 / 105
49 / 105
50 / 105
51 / 105
52 / 105
53 / 105
54 / 105
55 / 105
56 / 105
57 / 105
58 / 105
59 / 105
60 / 105
61 / 105
62 / 105
63 / 105
64 / 105
65 / 105
66 / 105
67 / 105
68 / 105
69 / 105
70 / 105
71 / 105
72 / 105
73 / 105
74 / 105
75 / 105
76 / 105
77 / 105
78 / 105
79 / 105
80 / 105
81 / 105
82 / 105
83 / 105
84 / 105
85 / 105
86 / 105
87 / 105
88 / 105
89 / 105
90 / 105
91 / 105
92 / 105
93 / 105
94 / 105
95 / 105
96 / 105
97 / 105
98 / 105
99 / 105
100 / 105
101 / 105
102 / 105
103 / 105
104 / 105
105
hous

In [31]:
pickle_obj(resps, 'full_data')

In [50]:
resps[0][-5].text

'<response><industries cand_name="Bennie G Thompson (D)" cid="N00003288" cycle="2018" origin="Center for Responsive Politics" source="https://www.opensecrets.org/members-of-congress/industries?cid=N00003288&amp;cycle=2018" last_updated="06/10/2019" ><industry industry_code="P03" industry_name="Transportation Unions" indivs="0" pacs="73000" total="73000" /><industry industry_code="P04" industry_name="Public Sector Unions" indivs="0" pacs="61500" total="61500" /><industry industry_code="K01" industry_name="Lawyers/Law Firms" indivs="34341" pacs="25000" total="59341" /><industry industry_code="E08" industry_name="Electric Utilities" indivs="1750" pacs="48000" total="49750" /><industry industry_code="P02" industry_name="Industrial Unions" indivs="0" pacs="40000" total="40000" /><industry industry_code="M01" industry_name="Air Transport" indivs="0" pacs="37000" total="37000" /><industry industry_code="P05" industry_name="Misc Unions" indivs="0" pacs="34000" total="34000" /><industry industr

In [90]:
# fortunately i've got the data saved locally so we can graph it

In [64]:
resps[0]

[{'name': 'Ralph Abraham (R)',
  'party': 'R',
  'id': 'N00036633',
  'Health Professionals': {'code': 'H01',
   'name': 'Health Professionals',
   'indiv': '32400',
   'pac': '55500',
   'total': '87900'},
  'Crop Production & Basic Processing': {'code': 'A01',
   'name': 'Crop Production & Basic Processing',
   'indiv': '30100',
   'pac': '52250',
   'total': '82350'},
  'Agricultural Services/Products': {'code': 'A07',
   'name': 'Agricultural Services/Products',
   'indiv': '750',
   'pac': '37500',
   'total': '38250'},
  'General Contractors': {'code': 'C01',
   'name': 'General Contractors',
   'indiv': '29100',
   'pac': '4500',
   'total': '33600'},
  'Air Transport': {'code': 'M01',
   'name': 'Air Transport',
   'indiv': '0',
   'pac': '30500',
   'total': '30500'},
  'Leadership PACs': {'code': 'Q03',
   'name': 'Leadership PACs',
   'indiv': '0',
   'pac': '29750',
   'total': '29750'},
  'Defense Aerospace': {'code': 'D01',
   'name': 'Defense Aerospace',
   'indiv': '0',

In [68]:
resps[0][199].text

'<response><industries cand_name="Walter B Jones Jr. (R)" cid="N00002299" cycle="2018" origin="Center for Responsive Politics" source="https://www.opensecrets.org/members-of-congress/industries?cid=N00002299&amp;cycle=2018" last_updated="06/10/2019" ><industry industry_code="Q10" industry_name="Misc Issues" indivs="111125" pacs="0" total="111125" /><industry industry_code="K01" industry_name="Lawyers/Law Firms" indivs="13175" pacs="18000" total="31175" /><industry industry_code="H01" industry_name="Health Professionals" indivs="12150" pacs="18000" total="30150" /><industry industry_code="W06" industry_name="Retired" indivs="24225" pacs="0" total="24225" /><industry industry_code="D01" industry_name="Defense Aerospace" indivs="0" pacs="19000" total="19000" /><industry industry_code="F10" industry_name="Real Estate" indivs="8500" pacs="10000" total="18500" /><industry industry_code="A01" industry_name="Crop Production &amp; Basic Processing" indivs="1525" pacs="16500" total="18025" /><in

In [18]:
resps = unpickle_obj('400_so_far')

In [27]:
resps_backup = resps

In [111]:
resps[0]

[{'name': 'Ralph Abraham (R)',
  'party': 'R',
  'id': 'N00036633',
  'Health Professionals': {'code': 'H01',
   'name': 'Health Professionals',
   'indiv': '32400',
   'pac': '55500',
   'total': '87900'},
  'Crop Production & Basic Processing': {'code': 'A01',
   'name': 'Crop Production & Basic Processing',
   'indiv': '30100',
   'pac': '52250',
   'total': '82350'},
  'Agricultural Services/Products': {'code': 'A07',
   'name': 'Agricultural Services/Products',
   'indiv': '750',
   'pac': '37500',
   'total': '38250'},
  'General Contractors': {'code': 'C01',
   'name': 'General Contractors',
   'indiv': '29100',
   'pac': '4500',
   'total': '33600'},
  'Air Transport': {'code': 'M01',
   'name': 'Air Transport',
   'indiv': '0',
   'pac': '30500',
   'total': '30500'},
  'Leadership PACs': {'code': 'Q03',
   'name': 'Leadership PACs',
   'indiv': '0',
   'pac': '29750',
   'total': '29750'},
  'Defense Aerospace': {'code': 'D01',
   'name': 'Defense Aerospace',
   'indiv': '0',

# Parse XML into nested list of nested dictionaries
- it's a lot cleaner than it sounds

- same [ [house], [chamber] ] structure
    - { name, party, id, industries },
        - industries: { oil:3600, pharma:12000, ... }

In [27]:
def parse_xml(resp): # parses member's xml to dictionary
    d = {}
    ec = 0
    try:
        root = ET.fromstring(resp.text)
        for child in (root.iter('*')):
            cd = child.attrib # child dictionary
            if child.tag == 'industries': # identification
                d['name'] = cd['cand_name']
                d['party'] = d['name'][-2:-1]
                d['id'] = cd['cid']
            elif child.tag == 'industry': # parse bribe
                bribe = {}
                bribe['code'] = cd['industry_code']
                bribe['name'] = cd['industry_name']
                bribe['indiv'] = cd['indivs']
                bribe['pac'] = cd['pacs']
                bribe['total'] = cd['total']
                d[bribe['name']] = bribe # key is industry name, value is dict
            # d should have identifying attributes + several dictionaries for each bribe
    except:
        ec +=1
    print(f'{ec} errors')
    return d

def parse_responses(resps): # returns list of member dicts (with nested dictionaries for each)
    out = []
    for chamber in resps:
        ch = []
        for c, member in enumerate(chamber):
            mem_dict = parse_xml(member)
            ch.append(mem_dict)
            print(f'{c}')
        out.append(ch)
    print(len(out[0]), len(out[1]))
    return out
            
        

In [85]:
resps[0] = resps[0][:198]

In [28]:
mems = parse_responses(resps)

0 errors
0
0 errors
1
0 errors
2
0 errors
3
0 errors
4
0 errors
5
0 errors
6
0 errors
7
0 errors
8
0 errors
9
0 errors
10
0 errors
11
0 errors
12
0 errors
13
0 errors
14
0 errors
15
0 errors
16
0 errors
17
0 errors
18
0 errors
19
0 errors
20
0 errors
21
0 errors
22
0 errors
23
0 errors
24
0 errors
25
0 errors
26
0 errors
27
0 errors
28
0 errors
29
0 errors
30
0 errors
31
0 errors
32
0 errors
33
0 errors
34
0 errors
35
0 errors
36
0 errors
37
0 errors
38
0 errors
39
0 errors
40
0 errors
41
0 errors
42
0 errors
43
0 errors
44
0 errors
45
0 errors
46
0 errors
47
0 errors
48
0 errors
49
0 errors
50
1 errors
51
0 errors
52
0 errors
53
0 errors
54
0 errors
55
0 errors
56
0 errors
57
0 errors
58
0 errors
59
0 errors
60
0 errors
61
0 errors
62
0 errors
63
0 errors
64
0 errors
65
0 errors
66
0 errors
67
0 errors
68
0 errors
69
0 errors
70
0 errors
71
0 errors
72
0 errors
73
0 errors
74
0 errors
75
0 errors
76
0 errors
77
0 errors
78
0 errors
79
0 errors
80
0 errors
81
0 errors
82
0 errors
83
0 

In [54]:
resps

[[{'name': 'Ralph Abraham (R)',
   'party': 'R',
   'id': 'N00036633',
   'Health Professionals': {'code': 'H01',
    'name': 'Health Professionals',
    'indiv': '32400',
    'pac': '55500',
    'total': '87900'},
   'Crop Production & Basic Processing': {'code': 'A01',
    'name': 'Crop Production & Basic Processing',
    'indiv': '30100',
    'pac': '52250',
    'total': '82350'},
   'Agricultural Services/Products': {'code': 'A07',
    'name': 'Agricultural Services/Products',
    'indiv': '750',
    'pac': '37500',
    'total': '38250'},
   'General Contractors': {'code': 'C01',
    'name': 'General Contractors',
    'indiv': '29100',
    'pac': '4500',
    'total': '33600'},
   'Air Transport': {'code': 'M01',
    'name': 'Air Transport',
    'indiv': '0',
    'pac': '30500',
    'total': '30500'},
   'Leadership PACs': {'code': 'Q03',
    'name': 'Leadership PACs',
    'indiv': '0',
    'pac': '29750',
    'total': '29750'},
   'Defense Aerospace': {'code': 'D01',
    'name': 'D

In [57]:
full400 = [[],[]]
full400[0] = resps[0][:198]
len(full400[0])

198

In [87]:
mems_backup = mems

In [154]:
len(mems[0])

200

In [25]:
mems[0][19]

{}

In [40]:
mems = mems_backup

In [26]:
print(len(mems[0]), len(mems[1]))

399 0


In [95]:

def clean_nulls(mems):
    print(len(mems[0]))
    c=0
    for chamber in mems:
        for n, mem in enumerate(chamber):
            print(n)
            if not mem: # if dict is empty. probably an id mismatch on my end
                c+=1 # i might have used 2016 IDs for the 2018 congress. big oops
                chamber.remove(mem)
                continue
            a = mem['name']
    print(f'{c} nulls removed')
    print(f"{len(mems[0])}")
    
clean_nulls(mems)

399
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
27

In [32]:
c=0
for mem in mems[0]:
    if not mem: c+=1
else:
    print(mem)
[print(c)]

{}
99


[None]

In [46]:
len(mems[0][97:])

201

In [29]:
mems

[[{'name': 'Ralph Abraham (R)',
   'party': 'R',
   'id': 'N00036633',
   'Health Professionals': {'code': 'H01',
    'name': 'Health Professionals',
    'indiv': '32400',
    'pac': '55500',
    'total': '87900'},
   'Crop Production & Basic Processing': {'code': 'A01',
    'name': 'Crop Production & Basic Processing',
    'indiv': '30100',
    'pac': '52250',
    'total': '82350'},
   'Agricultural Services/Products': {'code': 'A07',
    'name': 'Agricultural Services/Products',
    'indiv': '750',
    'pac': '37500',
    'total': '38250'},
   'General Contractors': {'code': 'C01',
    'name': 'General Contractors',
    'indiv': '29100',
    'pac': '4500',
    'total': '33600'},
   'Air Transport': {'code': 'M01',
    'name': 'Air Transport',
    'indiv': '0',
    'pac': '30500',
    'total': '30500'},
   'Leadership PACs': {'code': 'Q03',
    'name': 'Leadership PACs',
    'indiv': '0',
    'pac': '29750',
    'total': '29750'},
   'Defense Aerospace': {'code': 'D01',
    'name': 'D

In [84]:
mems

[[{}, {}, {}, {}, {}, {}, {}, {}, {}, {}, {}],
 [{}, {}, {}, {}, {}, {}, {}, {}, {}, {}, {}],
 [{}, {}, {}, {}, {}, {}, {}, {}, {}, {}, {}],
 [{}, {}, {}, {}, {}, {}, {}, {}, {}, {}, {}],
 [{}, {}, {}, {}, {}, {}, {}, {}, {}, {}, {}],
 [{}, {}, {}, {}, {}, {}, {}, {}, {}, {}, {}],
 [{}, {}, {}, {}, {}, {}, {}, {}, {}, {}, {}],
 [{}, {}, {}, {}, {}, {}, {}, {}, {}, {}, {}],
 [{}, {}, {}, {}, {}, {}, {}, {}, {}, {}, {}],
 [{}, {}, {}, {}, {}, {}, {}, {}, {}, {}, {}],
 [{}, {}, {}, {}, {}, {}, {}, {}, {}, {}, {}],
 [{}, {}, {}, {}, {}, {}, {}, {}, {}, {}, {}],
 [{}, {}, {}, {}, {}, {}, {}, {}, {}, {}, {}],
 [{}, {}, {}, {}, {}, {}, {}, {}, {}, {}, {}],
 [{}, {}, {}, {}, {}, {}, {}, {}, {}, {}, {}],
 [{}, {}, {}, {}, {}, {}, {}, {}, {}, {}, {}],
 [{}, {}, {}, {}, {}, {}, {}, {}, {}, {}, {}],
 [{}, {}, {}, {}, {}, {}, {}, {}, {}, {}, {}],
 [{}, {}, {}, {}, {}, {}, {}, {}, {}, {}, {}, {}],
 [{}, {}, {}, {}, {}, {}, {}, {}, {}, {}, {}],
 [{}, {}, {}, {}, {}, {}, {}, {}, {}, {}, {}],
 [{}, {},

In [89]:
print(len(mems[0]), len(unfmems[0]))

198 201


In [91]:
comp = [[],[]]
comp[0] = mems[0]+unfmems[0]
len(comp[0])

399

In [92]:
comp[0]

[{},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {},
 {'name': 

In [93]:
mems = comp

In [30]:
c=0 # check for duplicates
for chamber in mems:
    for c, mem in enumerate(chamber):
        a = mem['name']
        for mem in chamber: # double loop to check doubles
            b = mem['name']
            if a==b: c+=1
c -= len(mems[0])
print(f'{len(mems[0])} mems,  {c} matches' ) # we want no matches

KeyError: 'name'

In [51]:
mems

[[{'name': 'Ralph Abraham (R)',
   'party': 'R',
   'id': 'N00036633',
   'Health Professionals': {'code': 'H01',
    'name': 'Health Professionals',
    'indiv': '32400',
    'pac': '55500',
    'total': '87900'},
   'Crop Production & Basic Processing': {'code': 'A01',
    'name': 'Crop Production & Basic Processing',
    'indiv': '30100',
    'pac': '52250',
    'total': '82350'},
   'Agricultural Services/Products': {'code': 'A07',
    'name': 'Agricultural Services/Products',
    'indiv': '750',
    'pac': '37500',
    'total': '38250'},
   'General Contractors': {'code': 'C01',
    'name': 'General Contractors',
    'indiv': '29100',
    'pac': '4500',
    'total': '33600'},
   'Air Transport': {'code': 'M01',
    'name': 'Air Transport',
    'indiv': '0',
    'pac': '30500',
    'total': '30500'},
   'Leadership PACs': {'code': 'Q03',
    'name': 'Leadership PACs',
    'indiv': '0',
    'pac': '29750',
    'total': '29750'},
   'Defense Aerospace': {'code': 'D01',
    'name': 'D

In [31]:
pickle_obj(mems, 'json_data')
print('data saved!')

data saved!


# data ready for graphing
- continued in 'graphing' notebook